# Daily Dose of Data Science

This notebook accompanies the code for the post: [Building Multi-task Learning Models](https://blog.dailydoseofds.com/p/building-multi-task-learning-models)

Author: Avi Chawla

In [ ]:
import torch 
import torch.nn as nn
import numpy as np
import matplotlib.pyplot as plt

import seaborn as sns
sns.set()

## Generate data

In [ ]:
high = 2*np.pi
x = torch.unsqueeze(torch.linspace(-high, high, 20000), dim=1)
x = x[torch.randperm(x.shape[0])]

In [ ]:
random_sin = np.random.uniform(low=-0.01, high=0.01, size = (x.shape[0], ))
random_cos = np.random.uniform(low=-0.01, high=0.01, size = (x.shape[0], ))

In [ ]:
sin_y = (torch.sin(x[:, 0]) + random_sin).reshape(-1, 1).double()
cos_y = (torch.cos(x[:, 0]) + random_cos).reshape(-1, 1).double()

In [ ]:
plt.figure(figsize=(6, 4))
plt.scatter(x[:, 0].reshape(-1, 1), sin_y, s=20, label = "Sin")
plt.scatter(x[:, 0].reshape(-1, 1), cos_y, s=20, label = "Cos")
plt.legend()
plt.show()

## Define network

In [ ]:
class Net(nn.Module):
    
    def __init__(self, h):
        super(Net, self).__init__()
        
        self.model1 = torch.nn.Sequential(
                        torch.nn.Linear(x.shape[1], h),
                        torch.nn.ReLU(),
                        torch.nn.Linear(h, h),
                        torch.nn.ReLU(),
                        torch.nn.Linear(h, h),
                        torch.nn.ReLU()  
                        )
        
        self.model_sin = torch.nn.Sequential(
                        torch.nn.Linear(h, h),
                        torch.nn.ReLU(),
                        torch.nn.Linear(h, 1))
    
        self.model_cos = torch.nn.Sequential(
                        torch.nn.Linear(h, h),
                        torch.nn.ReLU(),
                        torch.nn.Linear(h, 1))
    
        
    def forward(self, inputs):
        
        x1 = self.model1(inputs)
        output_sin = self.model_sin(x1).double()
        output_cos = self.model_cos(x1).double()
        
        return output_sin, output_cos

## Train network

In [ ]:
epochs = 100
learning_rate = 0.01

In [ ]:
net = Net(150)
losses = []
loss_func = torch.nn.MSELoss()
optimizer = torch.optim.Adam(net.parameters(), lr=learning_rate)

for epoch in (range(epochs)):
    
    prediction = net(x)     

    loss1 = loss_func(prediction[0], sin_y)
    loss2 = loss_func(prediction[1], cos_y)

    loss = loss1 + loss2
    optimizer.zero_grad()  
    loss.backward()        
    optimizer.step() 
    
    losses.append(loss.item())
    
    if (epoch+1)%5==0:
        print("Epoch = ", epoch, "Loss = ", round(loss.item(), 3))

In [ ]:
plt.plot(losses[::5],'-o')
plt.xlabel('epoch')
plt.ylabel('losses')
plt.show()